
# Diagonal design of experiments

Here is an illustration of the diagonal design of experiments (DOE)
implemented by the :class:`.DiagonalDOE` class
and used by the :class:`.ScalableDiagonalModel`.
The idea is to sample the discipline by varying its inputs proportionally
on one of the diagonals of its input space.


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_design_space
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo.post.dataset.scatter_plot_matrix import ScatterMatrix

configure_logger()

## Create the discipline
First, we create an :class:`.AnalyticDiscipline`
implementing the function: $f(x)=2x-3\sin(2\pi y)$
and set its cache policy to ``"MemoryFullCache"``.



In [ ]:
discipline = create_discipline(
    "AnalyticDiscipline", expressions={"z": "2*x-3*sin(2*pi*y)"}
)

## Create the design space
Then, we create a :class:`.DesignSpace`
where $x$ and $y$ vary between 0 and 1.



In [ ]:
design_space = create_design_space()
design_space.add_variable("x", l_b=0.0, u_b=1.0)
design_space.add_variable("y", l_b=0.0, u_b=1.0)

## Sample with the default mode
Lastly, we create a :class:`.DOEScenario`
and execute it with the :class:`.DiagonalDOE` algorithm
to get 10 evaluations of $f$.
Note that we use the default configuration:
all the disciplinary inputs vary proportionally
from their lower bounds to their upper bounds.



In [ ]:
scenario = create_scenario(
    discipline, "DisciplinaryOpt", "z", design_space, scenario_type="DOE"
)
scenario.execute({"algo": "DiagonalDOE", "n_samples": 10})
dataset = scenario.to_dataset(opt_naming=False)
ScatterMatrix(dataset).execute(save=False, show=True)

## Sample with reverse mode for $y$
We can also change the configuration
in order to select another diagonal of the input space,
e.g. increasing $x$ and decreasing $y$.
This configuration is illustrated in the new :class:`.ScatterMatrix` plot
where the $(x,y)$ points follow the $t\mapsto -t$ line
while  the $(x,y)$ points follow the $t\mapsto t$ line
with the default configuration.



In [ ]:
scenario = create_scenario(
    discipline, "DisciplinaryOpt", "z", design_space, scenario_type="DOE"
)
scenario.execute(
    {"algo": "DiagonalDOE", "n_samples": 10, "algo_options": {"reverse": ["y"]}}
)
dataset = scenario.to_dataset(opt_naming=False)
ScatterMatrix(dataset).execute(save=False, show=True)